# Environment preparation


## import library


In [1]:
import pandas as pd


from Preprocessing import *

## Load data from rank table in Excel file


In [2]:
file_path = r"data\MolochTHbackup.xlsx"
df_raw = pd.read_excel(file_path, sheet_name=6, header=1, usecols=range(1, 8))
df_raw

d:\repos\CRK_guild_boss\.venv\Lib\site-packages\openpyxl\worksheet\_reader.py:329: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


Date  Season Round  Season\nRank  GuildPic   GuildName  \
0   2024-01-30      10  10-1            10       NaN          열매   
1   2024-01-30      10  10-1            11       NaN         무야호   
2   2024-01-30      10  10-1            12       NaN        재난경보   
3   2024-01-30      10  10-1            13       NaN  Peppermint   
4   2024-01-30      10  10-1            14       NaN    MolochTH   
..         ...     ...   ...           ...       ...         ...   
363 2024-06-04       4   4-4            16       NaN    Nobility   
364 2024-06-04       4   4-4            17       NaN        S7AR   
365 2024-06-04       4   4-4            18       NaN      DEKWAT   
366 2024-06-04       4   4-4            19       NaN        MyTH   
367 2024-06-04       4   4-4            20       NaN        쿠벤저스   

     Total Trophies  
0         8367945.0  
1         8217900.0  
2         8149795.0  
3         8000885.0  
4         7859975.0  
..              ...  
363             NaN  
364             NaN  
365             NaN  
366             NaN  
367             NaN  

[368 rows x 7 columns]

In [3]:
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 368 entries, 0 to 367
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Date            368 non-null    datetime64[ns]
 1   Season          368 non-null    int64         
 2   Round           368 non-null    object        
 3   Season
Rank     368 non-null    int64         
 4   GuildPic        0 non-null      float64       
 5   GuildName       368 non-null    object        
 6   Total Trophies  348 non-null    float64       
dtypes: datetime64[ns](1), float64(2), int64(2), object(2)
memory usage: 20.3+ KB


## Clean data

In [4]:
data = clean_data(df_raw.copy())
style_df(data)

In [5]:
style_df(data.describe())

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 286 entries, 0 to 285
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Date            286 non-null    datetime64[ns]
 1   Season          286 non-null    category      
 2   Round           286 non-null    category      
 3   GuildName       286 non-null    string        
 4   GuildNameExtra  286 non-null    string        
 5   Trophies        286 non-null    int64         
 6   SeasonTotal     286 non-null    int64         
 7   RoundRank       286 non-null    int32         
 8   DiffRoundRank   286 non-null    int32         
 9   SeasonRank      286 non-null    category      
 10  DiffSeasonRank  286 non-null    int32         
 11  Improvement     286 non-null    int32         
 12  GrowthRate      286 non-null    float64       
dtypes: category(3), datetime64[ns](1), float64(1), int32(4), int64(2), string(2)
memory usage: 20.4 KB


In [7]:
# max total must equal to sum of earned trophies for each season
compare_total = data.groupby(
    ["GuildName", "Season"], as_index=False, observed=True
).agg(
    maxTotal=("SeasonTotal", "max"),
    sumEarned=("Trophies", "sum"),
)

# display(compare_total)

compare_total["compare_result"] = compare_total.maxTotal == compare_total.sumEarned

# if all rows are true, sum of boonlean values must equal to number of rows
val_result = (compare_total.maxTotal == compare_total.sumEarned).sum() == len(
    compare_total
)

if not val_result:
    print(f"maxTotal = sumEarned : {val_result}\n")
    display(compare_total[compare_total.compare_result == False])
else:
    print(f"maxTotal = sumEarned : {val_result}")

maxTotal = sumEarned : False



GuildName Season  maxTotal  sumEarned  compare_result
48         秋      3  26826630    8942210           False

In [8]:
data.loc[(data.GuildName == "秋")]

Date Season Round GuildName GuildNameExtra  Trophies  SeasonTotal  \
224 2024-05-07      3   3-3         秋        秋 (aki)   8942210     26826630   

     RoundRank  DiffRoundRank SeasonRank  DiffSeasonRank  Improvement  \
224          1              0         20               0            0   

     GrowthRate  
224         0.0

In [9]:
style_df(data.loc[(data.GuildName == "재난경보")])

In [10]:
data[data.GrowthRate == data.GrowthRate.max()]

Date Season Round GuildName            GuildNameExtra  Trophies  \
238 2024-05-14      4   4-1      재난경보  재난경보 (jae-nan-gyeong-bo)  10269885   

     SeasonTotal  RoundRank  DiffRoundRank SeasonRank  DiffSeasonRank  \
238     10269885         13              7         13               1   

     Improvement  GrowthRate  
238      1044760   11.325158

In [11]:
max_date = str(data["Date"].max()).split(" ")[0]

max_round = data["Round"].max()

print(f"{max_round=}\n{max_date=}")

max_round='4-3'
max_date='2024-05-28'


# Save processed data in .csv format


In [12]:
data

Date Season Round  GuildName GuildNameExtra  Trophies  SeasonTotal  \
0   2024-02-27      1   1-1  Spearmint      Spearmint  10513190     10513190   
1   2024-02-27      1   1-1      Vivid          Vivid  10510940     10510940   
2   2024-02-27      1   1-1    Nobless        Nobless  10251975     10251975   
3   2024-02-27      1   1-1      LAODA          LAODA  10011795     10011795   
4   2024-02-27      1   1-1        미라클  미라클 (miracle)   9930645      9930645   
..         ...    ...   ...        ...            ...       ...          ...   
281 2024-05-28      4   4-3       MyTH           MyTH  10346185     30139130   
282 2024-05-28      4   4-3   Nobility       Nobility  10445040     30041855   
283 2024-05-28      4   4-3       S7AR           S7AR  10270005     29984580   
284 2024-05-28      4   4-3         감동  감동 (gam-dong)   9872795     29384460   
285 2024-05-28      4   4-3     DEKWAT         DEKWAT  10286850     29698740   

     RoundRank  DiffRoundRank SeasonRank  DiffSeasonRank  Improvement  \
0            1              0          1               0            0   
1            2              0          2               0            0   
2            3              0          3               0            0   
3            4              0          4               0            0   
4            5              0          5               0            0   
..         ...            ...        ...             ...          ...   
281         17             -1         16               0       401815   
282         16              2         17               1       570010   
283         19             -2         18              -1       327380   
284         20             -1         19               0        79735   
285         18              2         20               0       585060   

     GrowthRate  
0      0.000000  
1      0.000000  
2      0.000000  
3      0.000000  
4      0.000000  
..          ...  
281    4.040628  
282    5.772236  
283    3.292692  
284    0.814199  
285    6.030434  

[286 rows x 13 columns]

In [13]:
save_path = r"data\CRK_guild_boss.csv"

data.to_csv(save_path, index=False)

save_path = r"data\CRK_guild_boss.pkl"

data.to_pickle(save_path)

---


# try

In [14]:
style_df(data)

---

In [15]:
dict([("".join(["Diff", col]), col) for col in data.columns if "Rank" in col])

{'DiffRoundRank': 'RoundRank',
 'DiffDiffRoundRank': 'DiffRoundRank',
 'DiffSeasonRank': 'SeasonRank',
 'DiffDiffSeasonRank': 'DiffSeasonRank'}

In [16]:
data.columns.tolist()
# style_df(data)

['Date',
 'Season',
 'Round',
 'GuildName',
 'GuildNameExtra',
 'Trophies',
 'SeasonTotal',
 'RoundRank',
 'DiffRoundRank',
 'SeasonRank',
 'DiffSeasonRank',
 'Improvement',
 'GrowthRate']